# Creating Web Maps in Python with GeoPandas and Folium

## Introduction


In this post, I demonstrate the use of the Python package Folium to create a web map from a GeoDataFrame. Folium is built on the Leaflet javascript library, which is a great tool for creating interactive web maps. However, I use Python for all of my data wrangling and analytical tasks, so it's really nice to be able to have the web-mapping capabilities from within the same environment. The goal of this post is to demonstrate a workflow between GeoPandas and Folium that makes it really easy to create functional and visually appealing web maps in Python.

In this example, I plot the point locations of crimes in San Francisco, overlaid on a choropleth of census tract crime density. Viewing these two layers together on a web map creates a nice way to get an overall sense of crime distribution, while also being able to view individual crime information. As I demonstrate below, these Python packages provide a nice, clean, and customizable way of doing this.

In [1]:
#Import the necessary Python moduless
import pandas as pd
import geopandas as gpd
import numpy as np
from geopandas.tools import sjoin
import folium
from folium.plugins import MarkerCluster
from folium import IFrame
import shapely
from shapely.geometry import Point
import unicodedata
import pysal as ps

## Data Prep
In this section I create two GeoDataFrames: one of crime points and one of census tract boundaries with crime densities. Both of these will then be plotted on a web map as separate layers.

### Read in Crime Data and Create a GeoDataFrame
First I read in a CSV file of San Francisco Police Incidents for the current year into a Pandas DataFrame. I downloaded the raw data from the San Francisco [Open Data Portal](https://data.sfgov.org/). Because there are so many crime incidents, I select a subset of the data: crimes in the "assault" category that were committed in the last 10 days. As shown below, this leaves me with 329 police incidents. 


In [2]:
#Read in CSV file specifying date field and encoding. Sort by date
all_crime = pd.read_csv('SFPD_Incidents_-_Current_Year__2016_.csv', parse_dates = ['Date'],\
                        encoding = 'utf-8').sort_values('Date').reset_index(drop=True)

#Clean up the encoding on the Crime Description field 
all_crime.Descript = all_crime.Descript.apply(lambda x: unicodedata.normalize("NFKD", x))

#Create a field that contains a string representation of the date, for later use
all_crime['DateStr'] = all_crime.Date.apply(lambda x: x.strftime("%Y-%m-%d"))

#Identify those crimes that are categorized as assaults
is_assault = all_crime.Category == 'ASSAULT' 

#Identify those crimes that were committed in the most recent 10 days of the dataset
recent = all_crime.Date.isin(all_crime.Date.unique()[-10:]) 

#Subset the data to get assaults commited within the last 10 days
assaults = all_crime[is_assault & recent].drop_duplicates('IncidntNum').reset_index(drop = True)
assaults = assaults[['IncidntNum', 'Descript', 'DateStr', 'Time', 'Address','X', 'Y']]
'{} assaults in the last 10 days'.format(str(len(assaults)))

'329 assaults in the last 10 days'

I now want to convert the assault data Pandas DataFrame to a GeoPandas GeoDataFrame (a spatial version of the former). The raw crime data comes with lat/long coordinates, which I use these to create Shapely point geometry objects (these are the values in the "geometry" field for each record in a GeoDataFrame). I specify the spatial reference system as ESPG 4326 which represents the standard WGS84 coordinate system.

In [3]:
#First create a GeoSeries of crime locations by converting coordinates to Shapely geometry objects
#Specify the coordinate system ESPG4326 which represents the standard WGS84 coordinate system
assault_geo = gpd.GeoSeries(assaults.apply(lambda z: Point(z['X'], z['Y']), 1),crs={'init': 'epsg:4326'})

#Create a geodataframe from the pandas dataframe and the geoseries of shapely geometry objects
assaults = gpd.GeoDataFrame(assaults.drop(['X', 'Y'], 1), geometry=assault_geo)
assaults.head()

IncidntNum                     Descript     DateStr   Time  \
0   160885198         THREATS AGAINST LIFE  2016-10-30  14:20   
1   160883142  BATTERY OF A POLICE OFFICER  2016-10-30  02:00   
2   160883158                      BATTERY  2016-10-30  02:00   
3   160883073                      BATTERY  2016-10-30  01:35   
4   160882928  BATTERY OF A POLICE OFFICER  2016-10-30  00:29   

                          Address                                     geometry  
0        0 Block of MCALLISTER ST   POINT (-122.412596970637 37.7811192121542)  
1        400 Block of BROADWAY ST   POINT (-122.405065483077 37.7980134745487)  
2  500 Block of BUENAVISTAWEST AV  POINT (-122.443281739239 37.76645765488571)  
3          400 Block of POWELL ST   POINT (-122.408431861057 37.7887772719153)  
4              0 Block of HOFF ST   POINT (-122.420575720933 37.7641819463712)

### Calculate Census Tract Crime Density
Next, I read in a Shapefile of San Francisco Census Tracts, which I also downloaded from the SF Open Data Portal. With GeoPandas, I can read a Shapefile directly into Python really easily. Then in one line of code, I spatially join census tracts to assaults (determine the census tract of each assault), and generate counts of assaults per census tract. Note that I use the ```to_crs``` function to convert assaults to the same coordinate system as Census Tracts (EPSG 3310) prior to spatially joining them.

Lastly, I calculate the number of assaults per square mile, which is the metric that I'm interested in plotting.

In [4]:
#Read tracts shapefile into GeoDataFrame
tracts = gpd.read_file('sf_census_tracts.shp').set_index('CTFIPS10')

#Generate Counts of Assaults per Census Tract
#Spatially join census tracts to assaults (after projecting) and then group by Tract FIPS while counting the number of crimes
tract_counts = gpd.tools.sjoin(assaults.to_crs(tracts.crs), tracts.reset_index()).groupby('CTFIPS10').size()

#Calculate Assault Density, converting square meters to square miles.
tracts['AssaultsPSqMi'] = (tract_counts/(tracts.geometry.area*3.86102e-7)).fillna(0)
tracts = tracts.reset_index()
tracts.head()

CTFIPS10                                           geometry  \
0  06075010100  POLYGON ((-212660.1301711957 -20053.0335317570...   
1  06075010200  (POLYGON ((-212986.3528985226 -20191.607399463...   
2  06075010300  POLYGON ((-212512.5989250286 -20763.4272515336...   
3  06075010400  POLYGON ((-211456.8561540585 -20837.2873740978...   
4  06075010500  POLYGON ((-211050.6276144625 -20707.0181740056...   

   AssaultsPSqMi  
0       3.423806  
1      19.871972  
2       0.000000  
3       7.721341  
4      15.009851

## Using Folium to Plot Data
The general approach I take here is to first create a Folium basemap and then add layers to it: (1) a choropleth of census tracts, symbolized crime density, and (2) crime point locations. I write [pure functions](https://www.sitepoint.com/functional-programming-pure-functions/) where possible, but use global variables whenever we're mutating objects. I find this approach the most convenient when experimenting in Jupyter. Hopefully it will also expose Folium's API better.

Of course, were we deploying this as a module in production, we would wrap everything nicely in a function and keep all mutation within it. Parameters in, HTML out.

###  Choropleth Layer of Tract Crime Density
As its inputs, my choropleth function takes a Folium map object, a GeoDataFrame, the name of the feature ID field, and the name of the field whose values will be symbolized. 

Leaflet uses GeoJSON objects to plot vector geometries (GeoJSON is a data format that is used to represent geographical features along with their non-spatial attributes). I also specify the id field, which is used to link the geometry in the GeoJSON with the data in the GeoDataFrame.

Lastly, I allow the user to specify the number of classes and the classification scheme. At this point, Folium has limited map classification options, so I instead use Pysal's choropleth [map classfication module](http://pysal.readthedocs.io/en/latest/library/esda/mapclassify.html) classification options. I used "Fisher_Jenks", but we could have used instead "Equal_Interval", and "Quantiles". 

Below, I first create a basemap that is centered in San Francisco, and then I create a choropleth on this basemap specifying the Census Tract boundaries as well as the feature I want to encode as a colour gradient (Assaults Per Square Mile).

In [5]:
# Create SF basemap specifying map center, zoom level, and using the default OpenStreetMap tiles

crime_map = folium.Map([37.7556, -122.4399], zoom_start = 12)

# Convert the GeoDataFrame to WGS84 coordinate reference system

gdf_wgs84 = tracts.to_crs({'init': 'epsg:4326'})

# Generate list of breakpoints using specified classification scheme. 
# List of breakpoint will be input to choropleth method

threshold_scale = ps.esda.mapclassify.Fisher_Jenks(gdf_wgs84['AssaultsPSqMi'], k = 5).bins.tolist()

crime_map.choropleth(  geo_data = tracts
                     , data = gdf_wgs84
                     , columns = ['CTFIPS10', 'AssaultsPSqMi']
                     , key_on = 'feature.properties.{}'.format('CTFIPS10')
                     , fill_color = 'YlOrRd'
                     , fill_opacity = 0.6
                     , line_opacity = 0.2
                     , threshold_scale = threshold_scale
                     , legend_name = 'Census tracts - choropleth')

crime_map

### Create Crime Point Cluster Layer
I now add the layer of crime point locations. Rather than display each individual point, I use Leaflet's marker clustering feature, which makes it easier to visualize large numbers of points by grouping together those that are close to each other. I also created a red "plus" symbol for batteries, and a blue star for every other offence. Additionally, I use popups to display information about a particular crime when the user clicks on a point. Folium lets you create HTML-rich popups called IFrames. I use this feature only in the most basic form, just to display a few lines of information: crime description, date, time, and address. There are obviously much more creative things that can be done with an IFrame popup (tables, graphs, sub-maps, etc.) but for my purposes this is all I need. 

You will notice that using *pure* functions the task of creating rich HTML and markers is made simpler. We can easily understand what is going on, and compose these functions to achive the desired result.

Finally, we mutate the objects in our global scope by applying our pure functions.

In [6]:
def html(r):
    """
    Create some neat HTML for popup.
    Argument: pd.Series (row, use df.apply(html, axis=1))
    Returns: html string
    """
    return """
    <b>{0}</b><br>
    {1}<br>
    {2} {3}
    """\
        .format(r.Descript
                ,r.Address
                ,r.DateStr
                ,r.Time)

def marker(r):
    """
    Creates marker for folium use.
    Argument: pd.Series (row, use df.apply(marker, axis=1)
    Returns: folium.Marker object
    """
    popup_html = html(r)
    iframe = folium.IFrame(html=popup_html, width=300, height=100)
    popup = folium.Popup(iframe, max_width=2650)
    if r.Descript == 'BATTERY':
        icon = folium.Icon(color='red', icon='plus')
    else:
        icon = folium.Icon(color='blue', icon='star')
    return folium.Marker((r.geometry.y, r.geometry.x)
           ,icon=icon
          ,popup=popup)

# store markers in assaults DataFrame
assaults['marker'] = assaults.apply(marker, axis=1)

# create zoomable clusters
cluster = folium.plugins.MarkerCluster(name='assaults')
assaults.marker.apply(lambda x: cluster.add_child(x))
crime_map.add_child(cluster)

style_function = lambda x: {'fillOpacity': 0
                           ,'weight': 1
                           ,'opacity': 0.2
                           ,'color': 'black'
                           }

folium.GeoJson(  tracts
               , style_function = style_function
               , name='Census tracts - boundaries'
              ).add_to(crime_map)

# Add layer control to toggle on/off
folium.LayerControl().add_to(crime_map)

crime_map

I hope this was helpful in demonstrating some of the mapping capabilities of Leaflet accessed through the package Folium.  The functions I wrote provide a nice way of displaying two very common types of spatial data on a basemap and can obviously be tweaked to add more custom functionality.

But you want to send your work to a stakeholder, right? No problems. Save it into a html file and attach it to an email. It will work! 😊

In [7]:
# save HTML
crime_map.save('sf_assaults.html') 